# Hand In 3 - Frequent Itemsets, Random Walks and Sequence Segmentation
Due: May 15th 2020, 23:59

This is a mandatory handin to be done in groups of 2-3 students, who shall submit:
1. A report in **PDF format**. The report should contain your experimental results; and
2. Python code in a zip-file. 

The pdf should **not** be in the zip-file and your report should **not** be a part of the python code. 
In other words, your report should be self-contained and your code should be there to document
that you actually did what you claim :-).

Submission should be done in Blackboard by **May 15th 23.59**.

## Problem 1 - Frequent Itemsets
We have learned the Apriori and FP-Growth algorithms for mining frequent itemsets.

1. Develop an implementation of both.
2. Run an experiment and show to what extent FP-Growth has an advantage.

Obtain the anonymized real-world `retail market basket` data from: http://fimi.ua.ac.be/data/.
This data comes from an anonymous Belgian retail store, and was donated by Tom Brijs from Limburgs Universitair Centrum, Belgium. The original data contains 16,470 different items and 88,162 transactions. You may only work with the top-50 items in terms of occurrence frequency.

_Hint:_ We have used this dataset before.

In [2]:
import numpy as np
import networkx as nx
%matplotlib inline
import matplotlib.pyplot as plt
import random
import itertools

# Local imports
import sys
sys.path.append('../utilities')
from load_data import load_market_basket, load_dblp_citations

In [2]:
# Load the retail data
transactions = load_market_basket()

def filter_transactions(T, k=50):
    """
        Keep only the top k items in the transactions.
        Remove transactions that become empty.
    """
    # Count occurences of each item
    counts = [0] * 16470
    for t in T:
        for i in t:
            counts[i] += 1

    # Sort and select top k
    counts = np.array(counts)
    order  = np.argsort(counts)[::-1] # reverse the sorted order

    indexes_to_keep = order[:k]       # Keep the top k items
    index_set = set(indexes_to_keep)  # Convert to python set for efficiency

    # Filter transactions
    T_new = [t_ for t_ in  [list(filter(lambda i: i in index_set, t)) for t in T]  if t_]
    return T_new

T = filter_transactions(transactions, k=50)

In [6]:
# Tiny function for generating rules from tuples
# Ex: rule((1, 2), (5)) outputs "(1, 2) => (5)"
rule  = lambda lhs, rhs: "%s => %s" % (str(lhs), str(rhs)) # For generating rule strings


def listify(L):
    return [[l] for l in L]

def get_occurences(I, T):
    occurences = 0
    for t in T:
        contains_all = True
        for i in I:
            if not i in t:
                contains_all = False
                break
        if contains_all:
            occurences += 1
            
    return occurences
            
def get_all_items(T):
    items = []
    for t in T:
        for i in t:
            if not i in items:
                items.append(i)
    return items

def is_frequent(I, T, support):
    return get_occurences(I, T) / len(T) >= support


def join_pair(L1, L2):
    result = []
    
    for l1 in L1:
        result.append(l1)
    for l2 in L2:
        if not l2 in result:
            result.append(l2)
            
    return result

def contains(candidate, C_k):
    return get_occurences(candidate, C_k) > 0

def flatten(L):
    
    flat_list = []
    for sublist in L:
        for item in sublist:
            flat_list.append(item)
            
    return flat_list
   

def apriori_algorithm(T, support=0.05, min_confidence=0.7):
    """
        Apriori algorithm for mining association rules.
        Inputs:
            T:               A list of lists, each inner list will contiain integer-item-ids. 
                             Example: T = [[1, 2, 5], [2, 3, 4], [1, 6]]
            support:         The proportion of occurences needed to keep itemsets.
            min_confidence:  Minimum confidence for the algorithm to output the rule.
        
        Outputs:
            rules:           List of tuples [(rule:str, confidence:float), ... ]
                             Example: [("(1, 2) => (5)", 0.84), ("(3, 4) => (7)", 0.75)]
    """
    
    ### TODO Your code here
    items = get_all_items(T)
    k = 1
    C = [[]]
    L =  [[]]
    C.append(listify(items))
    
    while len(C[k]) > 0:
        print("k", k)
        
        # frequent itemset generation
        L.append([])
        for I in C[k]:
            if is_frequent(I, T, support):
                L[k].append(I)
        
        # candidate generation
        C.append([])
        for l1 in L[k]:
            for l2 in L[k]:
                candidate = join_pair(l1, l2)
                if len(candidate) == k+1:
                    if is_frequent(candidate, T, support):
                        if not contains(candidate, C[k+1]):
                            C[k+1].append(candidate)
        
        k += 1
    
    # find rules
    #rules = []
    #itemsets = flatten(L)
    #for X in itemsets:
    #    for Y in itemsets:
    #        candidate = join_pair(X, Y)
    #        if len(candidate) == len(X) + len(Y):
    #            confidence = get_occurences(candidate, T) / get_occurences(X, T)
    #            if confidence >= min_confidence:
    #                rules.append((rule(X, Y), confidence))
    
    
    ### TODO Your code here
    return flatten(C)

In [9]:
test_data = [['I1','I2','I5'],
             ['I2','I4'],
             ['I2','I3'],
             ['I1','I2','I4'],
             ['I1','I3'],
             ['I2','I3'],
             ['I1','I3'],
             ['I1','I2','I3','I5'],
             ['I1','I2','I3']]

#rules = apriori_algorithm(T, support=0.05, min_confidence=0.7)
#rules = sorted(rules, key=lambda x: x[1], reverse=True)

#print("%-8s \t %s" % ("Conf.", "Rule"))
#for r in rules:
#    print("%7.4f%% \t %s" % r[::-1])

apriori_algorithm(test_data, support=0.3, min_confidence=0.7)

k 1
k 2


[['I1'],
 ['I2'],
 ['I5'],
 ['I4'],
 ['I3'],
 ['I1', 'I2'],
 ['I1', 'I3'],
 ['I2', 'I3']]

In [3]:
def get_frequent_item_count_dict(T, support):
    frequent_item_count = {}
    all_item_count = {}
    items = []
    
    for t in T:
        for item in t:
            if item in all_item_count.keys():
                all_item_count[item]['count'] += 1
                items += [item]
            else:
                all_item_count[item] = {'count': 1, 'node_pointer': None, 'word': item}
    
    for item in items:
        if all_item_count[item]['count'] >= support: 
            frequent_item_count[item] = all_item_count[item]
            
    return frequent_item_count, items


def build_fp_tree(T, support):
    frequent_item_count, items = get_frequent_item_count_dict(T, support)
    
    fp_tree = {
        'parent': None,
        'children': {}, 
        'word_count': 1, 
        'link': None,
        'word': None
    }
            
    for transaction in T:
        contains_frequent_item = False
        for item in transaction:
            if item in frequent_item_count.keys():
                contains_frequent_item = True
                
        if not contains_frequent_item:
            continue
            
        no_unfreq_transaction = []
        for w in transaction: 
            if w in frequent_item_count.keys(): 
                no_unfreq_transaction +=[w]
            
        sorted_transaction = sorted(no_unfreq_transaction, key=lambda item: -frequent_item_count[item]['count'])
        
        current_node = fp_tree
        for item in sorted_transaction:
            current_children = current_node['children'].keys()
            
            if not item in current_children:
                current_node['children'][item] = {
                    'parent': current_node,
                    'children': {}, 
                    'word_count': 0, 
                    'link': None,
                    'word': item
                }
                if frequent_item_count[item]['node_pointer'] is None:
                    frequent_item_count[item]['node_pointer'] = current_node['children'][item]
                else:
                    tmp_node = frequent_item_count[item]['node_pointer']
                    while(tmp_node['link'] is not None): tmp_node = tmp_node['link']
                    tmp_node['link'] = current_node['children'][item]
                
            current_node['children'][item]['word_count'] += 1
            current_node = current_node['children'][item]
            
    return fp_tree, frequent_item_count


def get_prefixes_of_item(item):
    paths, counts = [], []
    current_node = item['node_pointer']
    
    while current_node is not None:
        path = []
        traversal_node = current_node['parent']

        while traversal_node['word'] is not None:
            path += [traversal_node['word']]
            traversal_node = traversal_node['parent']
        
        paths += [path]
        counts += [current_node['word_count']]
        current_node = current_node['link']
       
    return paths, counts


def get_intersection(l1, l2):
    intersection = []
    
    for item in l1:
        if item in l2:
            intersection += [item]
    
    return intersection

def get_many_intersection(list_of_lists):
    intersection = list_of_lists[0]
            
    for l in list_of_lists:
        intersection = get_intersection(intersection, l)    
    
    return intersection

def get_new_transaction_lists(paths, counts):
    transaction_list = []
    
    for i in range(len(paths)):
        for j in range(counts[i]):
            transaction_list += [paths[i]]
    
    return transaction_list


def fp_growth(T, support, suffix=None):
    """
        FPGrowth algorithm for mining frequent item sets.
        Inputs:
            T:                   A list of lists, each inner list will contiain integer-item-ids. 
                                 Example: T = [[1, 2, 5], [2, 3, 4], [1, 6]]
            support:             The proportion of occurences needed to keep itemsets.
            suffix:              For recursion.
        
        Outputs:
            frequent_itemsets:   List of frequent itemsets
                                 Example: [[1, 2, 5], [1, 6]]
    """
    fp_tree, frequent_item_count = build_fp_tree(T, support)
    
    if len(fp_tree['children'].keys()) == 0: return []
    
    frequent_patterns = []
    
    for item in frequent_item_count.keys():
        new_suffix = None
        if suffix is None: 
            frequent_patterns += [[item]]
            new_suffix = [item]
        else:
            frequent_patterns += [[item] + suffix]
            new_suffix = [item] + suffix
            
        paths, counts = get_prefixes_of_item(frequent_item_count[item])
        
        new_transactions = get_new_transaction_lists(paths, counts)
        
        conditional_fp_tree_frequent_items = fp_growth(new_transactions, support, new_suffix)
        
        for frequent_item in conditional_fp_tree_frequent_items:
            frequent_patterns += [frequent_item]
            
    return frequent_patterns

In [5]:
test_data = [['I1','I2','I5'],
             ['I2','I4'],
             ['I2','I3'],
             ['I1','I2','I4'],
             ['I1','I3'],
             ['I2','I3'],
             ['I1','I3'],
             ['I1','I2','I3','I5'],
             ['I1','I2','I3']]

test_data_basket = load_market_basket()

fp_growth(test_data_basket, 100)

38 [[39], [48, 39], [48], []]
39 [[]]
48 [[39], []]
39 [[]]
39 [[]]
48 [[39], []]
39 [[]]
32 [[], [48, 39], [38, 48, 39], [39], [38, 39], [48], [38, 48], [38]]
48 [[39], []]
39 [[]]
39 [[]]
38 [[48, 39], [39], [48], []]
48 [[39], []]
39 [[]]
39 [[]]
41 [[38, 39], [32], [38, 48, 39], [], [39], [48, 39], [32, 48, 39], [38, 48], [38], [48], [32, 38, 39], [32, 38, 48, 39], [32, 38], [32, 48], [32, 39], [32, 38, 48]]
38 [[39], [48, 39], [48], []]
39 [[]]
48 [[39], []]
39 [[]]
39 [[]]
32 [[], [48, 39], [38, 39], [38, 48, 39], [38], [48], [39], [38, 48]]
48 [[39], []]
39 [[]]
39 [[]]
38 [[39], [48, 39], [], [48]]
39 [[]]
48 [[39], []]
39 [[]]
48 [[39], []]
39 [[]]
36 [[41, 38, 39], [41, 38, 48, 39], [89, 38, 48, 39], [41, 38, 48], [237, 38, 39], [225, 38, 39], [38, 39], [38, 48], [38], [41, 38], [89, 41, 38, 39], [38, 48, 39], [32, 38, 39], [65, 41, 38, 48, 39], [39], [170, 38], [89, 41, 32, 38, 48, 39], [32, 38, 48, 39], [170, 89, 32, 38, 48, 39], [65, 41], [225, 41, 38, 39], [225, 41, 32, 3

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 [[48], [48, 39], [], [39]]
48 [[]]
39 [[48], []]
48 [[], [39]]
39 [[]]
39 [[]]
38 [[48], [41, 48, 39], [39], [], [48, 39], [41], [41, 48], [41, 39]]
39 [[]]
32 [[38, 41, 48, 39], [41, 48, 39], [48, 39], [38], [41], [39], [38, 48, 39], [], [48], [38, 41, 48], [41, 48], [41, 39], [38, 48], [38, 39], [38, 41, 39]]
71 [[48], [1905, 1428, 489, 1831, 805, 1103, 1481, 1513, 365, 571, 1578, 249, 89, 65, 41, 38, 48, 39], [604, 39], [4057, 3354, 3642, 402, 3194, 682, 2492, 60], [1067, 107, 49, 39], [2493, 2343, 384, 398, 438, 237, 41, 39], [880, 591, 1659, 208, 1715, 535, 677, 310, 225, 32], [4307, 128, 1043, 549, 604, 60, 310, 237, 32], [1327, 36, 38, 39], [232, 623, 809, 535, 45, 41, 48], [], [2186, 1004, 39], [39], [599, 206, 1014, 3316, 1698, 1198, 45, 592, 1327, 41, 48, 39], [3240, 5767, 220, 4207, 123, 413, 48], [2424, 2793, 2413, 3006, 978, 2184, 856, 41, 48, 39], [1332, 536, 1158, 39], [4801, 2069, 2239, 2775, 297, 740, 1327, 475, 89, 48, 39], [504, 38, 48, 39], [246, 2168, 48, 39], [15

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 [[39], []]
39 [[]]
39 [[]]
2592 [[2593, 2598, 1598, 2599, 2596, 785, 1000, 201, 255, 1327, 89, 48, 39], [2709, 3458, 2389, 1784, 272, 156, 549, 589, 48, 39], [286, 170, 41, 32, 38, 39], [1145, 3903, 4105, 47, 740, 592, 41, 38, 39], [2793, 2150, 2413, 3966, 749, 2749, 1808, 2492, 384, 1344, 23, 161, 604, 60, 89, 41, 48, 39], [15, 2353, 246, 65], [91, 5289, 1016, 98, 1591, 189, 2375, 910, 150, 789, 65, 41, 48, 39], [1426, 102, 2299, 2327, 2708, 4891, 1104, 278, 66, 56, 260, 570, 38], [36, 38, 48], [2521, 4265, 2393, 3483, 1433, 337, 2763, 615, 907, 652, 1557, 398, 1872, 1814, 488, 544, 589, 123, 1327, 41, 48], [1233, 1815, 1188, 2425, 1113, 976, 117, 185, 65, 38, 48, 39], [552, 32, 48], [3410, 1023, 4685, 824, 475], [], [2034, 2997, 338, 1146, 48], [36, 170, 38, 39], [2692, 364, 5289, 2210, 4143, 849, 1616, 772, 31, 824, 32, 48], [2870, 791, 2476, 83, 3827, 842, 2184, 885, 8978, 175, 65, 41, 32, 48, 39], [48, 39], [2709, 1390, 8985, 432, 675, 310, 39], [713, 769, 2056, 1435, 544, 255, 4

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 [[395, 1227, 892, 207, 1821, 1183, 2635, 10, 10515, 117, 438, 65, 32, 48], [2933, 5465, 3776, 3338, 1354, 2514, 50, 2991, 178, 1355, 45, 101, 225, 48, 39], [690, 1772, 2413, 837, 2115, 41, 32, 48], [4056, 2550, 3776, 3577, 1026, 1355, 279, 45, 175, 237, 225, 65, 41, 48, 39], [4445, 7129, 387, 2169, 2079, 1180, 1903, 1081, 1308, 993, 10444, 2168, 783, 89, 48, 39], [6403, 440, 334, 41], [10493, 662, 3294, 652, 176, 10491, 1783, 170, 225, 89, 38, 48, 39], [3808, 989, 4524, 497, 2208, 8985, 10, 225], [643, 39], [1056, 3596, 2786, 4282, 4552, 4643, 573, 85, 199, 718, 1308, 2254, 208, 1043, 535, 79, 310, 48], [1909, 5712, 4753, 1104, 1786, 415, 961, 107, 117, 49, 41, 48, 39], [4969, 152, 764, 2091, 237, 48, 39], [10499, 967, 10498, 159, 2692, 4886, 4221, 3202, 59, 1060, 104, 1010, 2629, 346, 1585, 1435, 2238, 48, 39], [105, 18, 32, 38], [12503, 1503, 2843, 82, 2135, 2080, 1987, 808, 186, 407, 48], [2630, 2598, 1126, 2958, 32, 48, 39], [4685, 704, 592, 9], [637, 7068, 12952, 909, 3973, 423, 

[[38],
 [39, 38],
 [48, 38],
 [39, 48, 38],
 [39],
 [48],
 [39, 48],
 [32],
 [48, 32],
 [39, 48, 32],
 [39, 32],
 [38, 32],
 [48, 38, 32],
 [39, 48, 38, 32],
 [39, 38, 32],
 [41],
 [38, 41],
 [39, 38, 41],
 [48, 38, 41],
 [39, 48, 38, 41],
 [39, 41],
 [32, 41],
 [48, 32, 41],
 [39, 48, 32, 41],
 [39, 32, 41],
 [38, 32, 41],
 [39, 38, 32, 41],
 [48, 38, 32, 41],
 [39, 48, 38, 32, 41],
 [48, 41],
 [39, 48, 41],
 [36],
 [41, 36],
 [39, 41, 36],
 [38, 39, 41, 36],
 [38, 41, 36],
 [48, 41, 36],
 [39, 48, 41, 36],
 [38, 39, 48, 41, 36],
 [38, 48, 41, 36],
 [38, 36],
 [39, 36],
 [38, 39, 36],
 [48, 36],
 [39, 48, 36],
 [38, 39, 48, 36],
 [38, 48, 36],
 [89, 36],
 [48, 89, 36],
 [38, 48, 89, 36],
 [39, 89, 36],
 [38, 39, 89, 36],
 [38, 89, 36],
 [237, 36],
 [39, 237, 36],
 [38, 39, 237, 36],
 [38, 237, 36],
 [225, 36],
 [39, 225, 36],
 [38, 39, 225, 36],
 [38, 225, 36],
 [32, 36],
 [39, 32, 36],
 [38, 39, 32, 36],
 [38, 32, 36],
 [41, 32, 36],
 [39, 41, 32, 36],
 [38, 39, 41, 32, 36],
 [38, 41

In [ ]:
load_market_basekt

## Problem 2 - Random Walks
We introduced the notion of hitting time, as the expected length of a random walk 
between two nodes; the expected number of steps before a simple random walk starting 
from a vertex $v$ reaches a vertex $u$. Your present task is to compute the average 
hitting time in the 
`cit-DBLP` dataset from the [citation dataset collection](http://networkrepository.com/cit.php) 
in the [Network Repository](http://networkrepository.com/networks.php).
Here, average is defined across all pairs of nodes, considered in both directions. 
You may ignore pairs that are not connected by a (directed) path. 
Implement an algorithm that computes this average hitting time and report your 
result.

_Hint:_ We have used this dataset before.

In [2]:
# Method will load a list of all pairs of nodes that are 
# connected to each other by an edge.
# Additionally, is will load precomputed positions for plotting nodes.
# It is, however, not a pretty plot but the computatio
edges, pos = load_dblp_citations()
print("Number of edges: ", len(edges))
print("Number of nodes: ", len(pos))
print("Position example: ", pos[1])

Number of edges:  49743
Number of nodes:  12591
Position example:  [0.03738057 0.02658339]


In [28]:
def random_walk(G, u, v, max_walk_length=100):    
    p = u
    for k in range(max_walk_length):
        neighbors = G.out_edges(p)
        neighbors = listify(neighbors)
        
        if len(neighbors) == 0: 
            return -1
        
        p = random.choice(neighbors)[0][1]

        if p == v:
            return k
        
    return -1

def hitting_time(G, n1, n2, k=10, max_walk_length=100):
    walk_lengths = []
    
    for _ in range(k):
        walk_length = random_walk(G, n1, n2, max_walk_length)
        
        if walk_length > 0:
            walk_lengths.append(walk_length)
    
    if len(walk_lengths) == 0:
        return 0
    
    return np.mean(walk_lengths)

def avg_hitting_time(G):
    nodes = nx.nodes(G)

    total_hitting_time = 0

    for n1 in nodes:
        for n2 in nodes:
            ht = hitting_time(G, n1, n2)
            total_hitting_time += ht


    average_hitting_time = total_hitting_time / (len(nodes) * len(nodes))
    
    return average_hitting_time

In [ ]:
G=nx.read_edgelist("../exercises/cit-DBLP.edges", nodetype=int).to_directed()

#G = nx.DiGraph()
#G.add_edges_from([(1, 4), (2, 3), (2, 5), (3, 1), 
#                  (4, 3), (5, 4), (5, 2), (5, 6), 
#                  (5, 3), (6, 3), (6, 0), (7, 1),  
#                  (7, 3), (0, 1)])

avg_hitting_time(G)

## Problem 3 - Sequence Segmentation
The Dynamic Programming algorithm for optimally segmenting a sequence $S$ of length $n$ 
into $B$ segments, that we have introduced, is expressed by the following recursive equation:

$$
E(i, b) = \min_{j < i}\left[ E(j, b-1) + Err(j+1, i)\right]
$$

where $Err(j+1, i)$ is the error of a segment that contains items from $j+1$ to $i$.

Answer the following questions:

**1. What is the default space-complexity of this algorithm?**

The complexity of this algorithms depends on the segment length $B$ and the number of items $N$, so we can approximate it as $O(B\cdot N)$


**2. If we are willing to recompute some tabulated results, can we then reduce the 
    default space-complexity? _Exactly how_? What is the space-complexity then?**


    
**3. What is the cost of using the above space-efficiency technique in terms of time-complexity?**




**4. For the sub-problem of segmenting the $i$-prefix of sequence $S$ into $b$ segments, consider 
    the segment $M(i, b)$ that contains (if such segment exists) the middle item of 
    index $\lfloor \frac{n}{2} \rfloor$. The boundaries of $M(i, b)$ can be detected and tabulated 
    along with each $E(i, b)$ solution. Based on this observation, devise a method that reduces 
    the time-complexity burden identified in (3). 
    _(hint: use [divide-and-conquer](https://en.wikipedia.org/wiki/Divide-and-conquer_algorithm))_**
    
    
**5. What is the time complexity when using the technique proposed in (4)?**



**Disclaimer:** 
As this is the final handin and we are getting close to the exam, rehandins are not an option.
Therefor, we strongly encourage you to get started early and if you get too stuck, make sure
to send Frederik an email early (not right up to the deadline). For a faster reply, use
[fhvilshoj@cs.au.dk](mailto:fhvilshoj@cs.au.dk) and **not** ~201206000@ post.au.dk~. 

For those of you, who are not used to analyzing algorithms: by time-complexity and space-complexity, 
we refer to the theoretical computation time and memory usage, respectively, as a function of the problem size, i.e., as a 
function of $n$ and $B$ in Problem 3. We use [Big O notation](https://en.wikipedia.org/wiki/Big_O_notation)
to specify this. You should **not** infer it by implementing it in practice ;-) 
Again, when in doubt, shoot Frederik an email. 